In [ ]:
from semantic_search import SemanticSearch
import pandas as pd

df = pd.read_csv('all_articles_2020_2022_11_15.csv').dropna().reset_index(drop=True)

In [ ]:
import spacy
nlp = spacy.load('en_core_web_md')


In [ ]:
s = SemanticSearch(df, nlp)

In [ ]:
sentences = s.sentence_tokenize()

In [ ]:
sentences

In [4]:
from sentence_transformers import SentenceTransformer, util
model_name = 'msmarco-MiniLM-L-6-v3'
model = SentenceTransformer(model_name)

In [1]:
import pandas as pd

df = pd.read_csv('all_articles_2020_2022_11_15.csv').dropna().reset_index(drop=True)

In [9]:
import nltk
nltk.download('punkt')

sentences = df.copy()
sentences['sents'] = sentences['text'].apply(nltk.sent_tokenize)
sentences = sentences[['sents']]
sentences = sentences.explode('sents')
sentences = sentences.reset_index().rename(columns={'index':'org_index'})

[nltk_data] Downloading package punkt to /Users/pnadel01/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
import torch
torch.has_mps

True

In [5]:
device = torch.device('mps')
model.to(device)

SentenceTransformer(
  (0): Transformer({'max_seq_length': 512, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False})
)

In [6]:
device

device(type='mps')

In [11]:
from tqdm import tqdm
tqdm.pandas()

#sentences.sents.progress_apply(model.encode)

In [27]:
embeds = sentences.sents[:1000].progress_apply(model.encode)

100%|██████████| 1000/1000 [00:27<00:00, 35.89it/s]


In [28]:
import numpy as np
embeds.to_numpy()

array([array([ 0.60316855,  0.6242569 ,  0.64014614, -0.01467308,  0.02073613,
              -0.45712414, -0.25983533,  0.32890376, -0.31575114,  0.03792134,
               0.15155171, -0.42340663, -0.35632572,  0.02922854, -0.25540605,
              -0.07757353,  1.0614392 ,  0.43855366,  0.10020152,  0.15323557,
              -0.1851412 ,  0.29937696, -0.57348895,  0.3631151 , -0.30051044,
               0.37335482,  0.32033932,  0.6469835 , -0.04615869, -0.11230817,
               0.27940342,  1.0718402 , -0.35902086,  0.16153316, -0.24731512,
              -0.46950552, -0.16295804,  0.73477936,  0.47416794, -0.5201365 ,
               0.3810781 ,  0.8475835 ,  0.05979465,  0.17730767, -0.6268349 ,
              -0.42885256,  0.23247285, -0.42860982,  0.04914252,  0.37500033,
               0.6378712 , -0.2863147 , -0.58347744, -0.5926256 , -0.75172037,
              -0.41893172,  0.36416897,  1.4359666 , -0.01817242,  0.6698316 ,
              -0.11445568, -0.08789101,  0.03209021,

In [29]:
import umap
reducer = umap.UMAP()
reduced = reducer.fit_transform(embeds.to_list())

In [ ]:
search = ''
search_emb = model.encode(search)
